# QTrap The Cat

### Summary

`QTrap The Cat` is a quantum version of a classical game [Trap The Cat](https://trap-thecat.com/), where player is challenged by a Schrödinger's cat, which tries to escape from the given field by using not only usual moves, but also superposition of moves and entangled moves.

> Authors: Domrachev Ivan, Igor Alentev \
> Stack: ipycanvas, ipywidgets, qiskit

### Intructions to launch

To play the game, run whole jupyter notebook once. After that, executing the last cell would be enough to play the game. Detailed rules are listed right before the game.

# Configuration
Ignore any errors in case they happen.

## Known Issues
- In case your notebook loops on "Loading widget...",
try reloading the page, this should work most of the time. Drawing in 
remote environment is not the most stable feature.

In [1]:
!conda install -y -c conda-forge nodejs ipyevents ipycanvas

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.12.0
  latest version: 4.14.0

Please update conda by running

    $ conda update -n base conda



# All requested packages already installed.



In [2]:
!jupyter labextension install @jupyter-widgets/jupyterlab-manager ipycanvas

An error occurred.
ValueError: Please install nodejs >=12.0.0 before continuing. nodejs may be installed using conda or directly from the nodejs website.
See the log file for details:  /tmp/jupyterlab-debug-0es0dpbo.log


In [3]:
from qiskit import QuantumCircuit, QuantumRegister, Aer
from qiskit.circuit.classicalregister import Clbit
from qiskit.quantum_info.operators import Operator
from qiskit.circuit.library.arithmetic import VBERippleCarryAdder
from qiskit.circuit.library import XGate
from qiskit.extensions.unitary import UnitaryGate
from qiskit.quantum_info import Statevector
from qiskit.compiler import transpile

from matplotlib.backends.backend_agg import FigureCanvasAgg as FigureCanvas
from matplotlib.figure import Figure
import os

from collections import deque
from random import randint, sample
from IPython.display import display
from math import log2, ceil

import ipycanvas as ic
import ipywidgets as iw
import ipyevents as ie
import numpy as np
import random
import math
import cmath

import time
import threading

## Cat simulators

Before implementing cat's, it's important to prepare increment gates fabrique to use it further on.

In [4]:
def get_increment_gate(ndims=6):
    """ Implements gate U|x> = |x+1>"""

    qc = QuantumCircuit(ndims)

    # Calculating carry, starting from the MSB
    for i in range(ndims - 1, 0, -1):
        cx_gate = XGate().control(i)
        qc.append(cx_gate, range(i + 1))

    # Adding 1 bitwise to the LSB
    qc.x(0)

    return qc.to_gate(label='++')


def get_decrement_gate(ndims=6):
    ''' Implements gate U|x> = |x-1>. Reverse of increment gate'''

    qc = QuantumCircuit(ndims)

    # Reverse order compared to increment gate
    qc.x(0)
    for i in range(1, ndims):
        cx_gate = XGate().control(i)
        qc.append(cx_gate, range(i + 1))

    return qc.to_gate(label='--')

There exist two versions of cats' classes:
 * `SimulatorCat` -- uses quantum coordinates and operations to make moves. Runs on the quantum simulator
 * `QuantumCat` -- uses only hadamard gates to create superpositions of moves. Runs on the quantum computers

Since the first implementation is more interesting, as well as it works faster then accessing quantum computer, we would proceed using the `SimulatorCat`

In [5]:
class SimulatorCat():
    def __init__(self, lim=(7, 7), init_pos=(3, 4)):
        self.lim = lim

        # Calculating, how many (qu)bits needed to store x and y coordinates
        self.x_qubits = ceil(log2(lim[0]))
        self.y_qubits = ceil(log2(lim[1]))
        self.hm_pos_qubits = self.x_qubits + self.y_qubits
        self.hm_helper_qubits = 0

        # Creating the circuit, which stores current gates list
        self.circuit = QuantumCircuit(self.hm_pos_qubits, self.hm_pos_qubits)

        # Setting initial cat position
        self._set_pos(init_pos)

        # Preparing gates, which would represent cat moves
        circuits_list = [QuantumCircuit(self.hm_pos_qubits) for i in range(6)]
        decrement_x_gate = get_decrement_gate(self.x_qubits)
        increment_x_gate = get_increment_gate(self.x_qubits)
        decrement_y_gate = get_decrement_gate(self.y_qubits)
        increment_y_gate = get_increment_gate(self.y_qubits)

        for i in range(6):
            direction = (i + 1) % 6
            if direction == 0 or direction == 5:
                circuits_list[i].append(decrement_x_gate,
                                        range(self.x_qubits))
            elif direction == 2 or direction == 3:
                circuits_list[i].append(increment_x_gate,
                                        range(self.x_qubits))
            if direction < 3:
                circuits_list[i].append(decrement_y_gate,
                                        range(self.x_qubits, self.x_qubits + self.y_qubits))
            else:
                circuits_list[i].append(increment_y_gate,
                                        range(self.x_qubits, self.x_qubits + self.y_qubits))
            if direction == 1:
                circuits_list[i].append(decrement_y_gate,
                                        range(self.x_qubits, self.x_qubits + self.y_qubits))
            if direction == 4:
                circuits_list[i].append(increment_y_gate,
                                        range(self.x_qubits, self.x_qubits + self.y_qubits))
                
        self.move_gates = [circuits_list[i].to_gate(label=f'Move {i}') for i in range(len(circuits_list))]

    def _set_pos(self, pos=(0, 0)):

        ''' Sets the position of the cat to the given one'''

        assert 0 <= pos[0] < self.lim[0] and 0 <= pos[1] < self.lim[1]

        (x, y) = pos

        for i in range(self.x_qubits):
            if x % 2 == 1:
                self.circuit.x(i)
            x //= 2

        for i in range(self.y_qubits):
            if y % 2 == 1:
                self.circuit.x(self.x_qubits + i)
            y //= 2

    def show_circuit(self, decompose=False):

        ''' 
            Visualise the current circuit. If decompose = True, then all gates
            are broke down to simpler gates
        '''

        if decompose:
            return self.circuit.decompose().draw('mpl')
        else:
            return self.circuit.draw('mpl')

    def show_state(self):

        '''Shows latex state of qubit. Does not work properly with superposition'''

        state = Statevector.from_int(0, 2 ** (self.hm_pos_qubits + self.hm_helper_qubits))
        state = state.evolve(self.circuit)
        display(state.draw('latex'))

    def measure_position(self):

        '''Measures current cat position and resets circuit'''

        # Adding measurent operator
        for i in range(self.hm_pos_qubits):
            self.circuit.measure(i, i)
        
        # Running circuit on the backend
        backend = Aer.get_backend('statevector_simulator')
        job = backend.run(transpile(self.circuit, backend))
        result = next(iter(job.result().get_counts().keys()))

        # Coordinates of the cat
        measured_pos = (
            int(result[self.x_qubits:], 2),
            int(result[:self.y_qubits], 2),
        )

        # Resetting circuit and setting up current position
        self.circuit = QuantumCircuit(self.hm_pos_qubits, self.hm_pos_qubits)
        self.hm_helper_qubits = 0
        self._set_pos(measured_pos)
        
        return measured_pos
        
        
    def _add_qubit(self):

        '''Adding extra qubit to the circuit. Returns its position in circuit'''

        self.hm_helper_qubits += 1

        help_reg_name = 'helper' + str(self.hm_helper_qubits)
        help_reg_pos = self.circuit.num_qubits

        helper_register = QuantumRegister(size=1, name=help_reg_name)
        self.circuit.add_register(helper_register)

        return help_reg_pos

    def superposition_move(self, directions):

        ''' 
            Creates superposition of given moves. Creates extra qubit.
            Only two moves are supported yet
        '''

        assert len(directions) == 2

        help_reg_pos = self._add_qubit()

        # Preparing corresponding versions of controlled move gates
        controlled_gates = [
            self.move_gates[directions[0]].control(1, ctrl_state=0),
            self.move_gates[directions[1]].control(1, ctrl_state=1)
        ]

        # Creating superposition and applying controlled versions of moves
        self.circuit.h(help_reg_pos)
        for gate in controlled_gates:
            self.circuit.append(gate, [help_reg_pos] + [i for i in range(self.hm_pos_qubits)])

    def entangled_move(self, pos, direction):

        ''' Creating a move, entangled from a given position. Uses extra qubit. '''

        help_reg_pos = self._add_qubit()

        # Encoding given position into right bit string
        get_bin = lambda x, n: format(x, 'b').zfill(n)
        ctrl = f'{get_bin(pos[1], self.y_qubits)}{get_bin(pos[0], self.x_qubits)}'

        # Creating CNOT gate with state as given position
        cx = XGate().control(self.hm_pos_qubits, ctrl_state=ctrl)
        # Creating controlled version of the move
        controlled_move = self.move_gates[direction].control(1)

        self.circuit.append(cx, [i for i in range(self.hm_pos_qubits)] + [[help_reg_pos]])
        self.circuit.append(controlled_move, [help_reg_pos] + [i for i in range(self.hm_pos_qubits)])

    def move(self, direction):

        '''Moving the cat in a given direction from 0 to 5.
           Direction of a move counts like this:
                _0_
             5 /   \ 1
             4 \   / 2
                ‾3‾
        '''
        assert 0 <= direction < 6
        self.circuit.append(self.move_gates[direction], range(self.hm_pos_qubits))

In [6]:
# Libraries to run program on the real quantum computer software
from qiskit import QuantumCircuit, transpile, Aer, IBMQ, execute
from qiskit.providers.ibmq import least_busy

In [7]:
class QuantumCat():
    def __init__(self, lim=(7, 7), init_pos=(3, 4)):
        self.lim = lim

        # Storing all the positions the cat might be in
        self.positions = [init_pos]
        self.hm_qubits = 0

        self.circuit = QuantumCircuit(0, 10)
        
        self.backend = None
        self.__load_backend__()
        
        
    def __load_backend__(self):
        
        ''' Loads Quantum Computer'''
        
        IBMQ.load_account()
        provider = IBMQ.get_provider(hub='ibm-q')
        self.backend = least_busy(
            provider.backends(filters=lambda x: x.configuration().n_qubits > 5
                              and not x.configuration().simulator)
        )
        print(self.backend.name())
        
    def _coords_shift(self, direction):

        '''Returns the shift of the coordinates, which corresponds to the given direction'''

        ans = [0, 0]
        direction = (direction + 1) % 6

        if direction == 0 or direction == 5:
            ans[0] -= 1
        elif direction == 2 or direction == 3:
            ans[0] += 1

        if direction < 3:
            ans[1] -= 1
        else:
            ans[1] += 1

        if direction == 1:
            ans[1] -= 1
        if direction == 4:
            ans[1] += 1
            
        return tuple(ans)

    def _add_qubit(self):

        '''Adding extra qubit to the circuit. Returns its position in circuit'''

        self.hm_qubits += 1

        help_reg_name = 'helper' + str(self.hm_qubits)
        help_reg_pos = self.circuit.num_qubits

        # Adding both new qubit and classical bit to the circuit
        helper_register = QuantumRegister(size=1, name=help_reg_name)
        self.circuit.add_register(helper_register)
       
        return help_reg_pos

    def show_circuit(self, decompose=False):

        ''' 
            Visualise the current circuit. If decompose = True, then all gates
            are broke down to simpler gates
        '''

        if decompose:
            display(self.circuit.decompose().draw('mpl'))
        else:
            display(self.circuit.draw('mpl'))

    def show_positions(self):

        ''' Shows current cat positions'''

        print(*self.positions)

    def _shift_pos(self, pos, shift):

        '''Shifts given position on the given shift'''

        return (pos[0] + shift[0], pos[1] + shift[1])

    def _apply_shift(self, idx, shift):

        '''Applies shift to the i-th position'''

        self.positions[idx] = self._shift_pos(self.positions[idx], shift)

    def measure_position(self):

        '''Measures current cat position and resets circuit'''

        cur_pos = tuple()

        if (self.hm_qubits == 0):
            # Only one position, cat is not in a superposition
            cur_pos = self.positions[0]
        else:
            for i in range(self.hm_qubits):
                self.circuit.measure(i, i)
            
            print('Starting execution...')
            job = execute(self.circuit, self.backend)
            print('Executed!')
            print(job.status())
            result = next(iter(job.result().get_counts().keys()))
            print('Got result')
            # Converting string result to the number and getting cat's position
            result_num = int(result, 2)
            cur_pos = self.positions[result_num]

            # Resetting circuit
            self.hm_qubits = 0
            self.positions = [cur_pos]
            self.circuit = QuantumCircuit(0, 10)

        return cur_pos

    def superposition_move(self, directions):

        ''' 
            Creates superposition of given moves. Creates extra qubit.
            Only two moves are supported yet
        '''
        assert len(directions) == 2

        shifts = [self._coords_shift(direction) for direction in directions]

        # Adding new qubit 'q' in a |+> state
        qubit_pos = self._add_qubit()
        self.circuit.h(qubit_pos)

        # Recalculating all positions:
        for i in range(len(self.positions)):
            # If M(q) = |1>, then the cat moves in the second direction
            self.positions.append(self._shift_pos(self.positions[i], shifts[1]))
            # If M(q) = |0>, then the cat moves in the first direction
            self._apply_shift(i, shifts[0])

    def entangled_move(self, pos, direction):

        ''' Creating a move, entangled from a given position.'''

        for i in range(len(self.positions)):
            # If there is a given position in a list of possibe cat positions,
            # then shift it in a given direction
            if self.positions[i] == pos:
                self._apply_shift(i, self._coords_shift(direction))

    def move(self, direction):

        '''Moving the cat in a given direction from 0 to 5'''

        # Calculating a shift and apply it to all the positions
        shift = self._coords_shift(direction)
        for pos_idx in range(len(self.positions)):
            self._apply_shift(pos_idx, shift)

## Artificial intelligence

The following class uses pathfinding algorithms ans non-trivial decision making to challenge the player as much as possible. Notice, that one of the directions for further development of our game is to improve AI and make it a stronger opponent. 

In [8]:
class AI() :
    def __init__(self, lim=(7, 7), init_pos=(3, 4)):
        self.lim = lim
        self.cur_poses = [init_pos]
        self.adj_vtx = self.__generate_field__()
    
   
    def __shift_in_direction__(self, pos, direction):
        
        '''Shifts given position into a given direction'''
        
        assert 0 <= direction < 6
        new_pos = tuple()
        
        if pos[0] % 2 == 0:
            if direction == 0:
                new_pos = (pos[0], pos[1] - 1)
            elif direction == 1:
                new_pos = (pos[0] + 1, pos[1] - 1)
            elif direction == 2:
                new_pos = (pos[0] + 1, pos[1])
            elif direction == 3:
                new_pos = (pos[0], pos[1] + 1)
            elif direction == 4:
                new_pos = (pos[0] - 1, pos[1])
            elif direction == 5:
                new_pos = (pos[0] - 1, pos[1] - 1)
        else:
            if direction == 0:
                new_pos = (pos[0], pos[1] - 1)
            elif direction == 1:
                new_pos = (pos[0] + 1, pos[1])
            elif direction == 2:
                new_pos = (pos[0] + 1, pos[1] + 1)
            elif direction == 3:
                new_pos = (pos[0], pos[1] + 1)
            elif direction == 4:
                new_pos = (pos[0] - 1, pos[1] + 1)
            elif direction == 5:
                new_pos = (pos[0] - 1, pos[1])
        return new_pos
                           
     
    def __detect_direction__(self, p_from, p_to):
        
        '''Given two positions, return the direction of the move'''
        
        for direction in range(6):
            if self.__shift_in_direction__(p_from, direction) == p_to:
                return direction
        raise RuntimeError("Invalid move!")
    
    
    def __generate_field__(self):
        
        '''Generates the adjacency matrix (dict) of the field'''
        
        adj_dict = dict()
        for x in range(self.lim[0]):
            for y in range(self.lim[1]):
                adjacent_vertices = list(
                    filter(
                        lambda v: 0 <= v[0] < self.lim[0] and 0 <= v[1] < self.lim[1], 
                        [self.__shift_in_direction__((x, y), i) for i in range(6)]
                    )
                )
                adj_dict[(x, y)] = adjacent_vertices

        return adj_dict
    
    
    def __is_field_border__(self, pos):
        
        '''Checks if the given position is on the border'''
        
        return pos[0] == 0 or pos[0] == self.lim[0]-1 or \
               pos[1] == 0 or pos[1] == self.lim[1]-1
    
    
    def __dfs__(self, init_pos):
        
        '''Implements DFS and returns the shortest pathes to the end
           for every adjacent position'''
        
        neighbours = self.adj_vtx[init_pos]
        
        if self.__is_field_border__(init_pos):
            return [[init_pos]]
        
        answer = []
        
        for start_pos in neighbours:
            path = [start_pos]

            visited_vertices = dict()
            visited_vertices[start_pos] = init_pos

            q = deque()
            q.appendleft(start_pos)

            while len(q) != 0:
                cur_pos = q.pop()

                if self.__is_field_border__(cur_pos):
                    it = cur_pos
                    path_q = deque()
                    path_q.appendleft(it)

                    while it != init_pos:
                        it = visited_vertices[it]
                        path_q.appendleft(it)
                    answer.append(list(path_q))

                    break

                for position in self.adj_vtx[cur_pos]:
                    if not position in visited_vertices:
                        q.appendleft(position)
                        visited_vertices[position] = cur_pos

        return answer
    
    
    def __apply_move__(self, move):
        
        ''' Apply given move to the position'''
        
        (move_type, args) = move
        
        if move_type == 0:
            direction = args
            for i in range(len(self.cur_poses)):
                self.cur_poses[i] = self.__shift_in_direction__(self.cur_poses[i], 
                                                                direction)
        elif move_type == 1:
            directions = args
            assert len(directions) == 2
            
            for i in range(len(self.cur_poses)):
                self.cur_poses.append(self.__shift_in_direction__(self.cur_poses[i],
                                                                  directions[1]))
                self.cur_poses[i] = self.__shift_in_direction__(self.cur_poses[i], 
                                                                directions[0])
        elif move_type == 2:
            (p_from, direction) = args
            
            for i in range(len(self.cur_poses)):
                if self.cur_poses[i] == p_from:
                    self.cur_poses[i] = self.__shift_in_direction__(self.cur_poses[i],
                                                                    direction)
        elif move_type == 3 or move_type == 4:
            self.cur_poses = None
            
            
        else:
            raise RuntimeError("Invalid move")
    
    
    def cat_measured(self, pos):
        
        ''' Sets the measured cat position'''
        
        self.cur_poses = [pos]
    
    
    def remove_vertex(self, v):
        
        ''' Removes the vertex from adjacency list'''
        
        for adj_v in self.adj_vtx[v]:
            self.adj_vtx[adj_v].remove(v)
        
        del self.adj_vtx[v]
    
      
    def make_move(self, debug = False):
        
        '''
            Deciding, which move to make. Return type -- move, with the following
            specification:
                move = (int, args), where int -- type of move:
                * 0 — usual move; args -- move direction
                * 1 — superposition move, args -- list of moves directions
                * 2 — entangled move, args -- initial point and direction
                * 3 — measurement move, args -- none
                * 4 — consede, args -- none
        '''
        
        debug_str = str()
        
        
        debug_str += 'AI is working...\n'
        debug_str += 'Current positions of the cat:\n'
        debug_str += f'    {self.cur_poses}\n'
        debug_str += '-'*40 +'\n' 
        
        
        # Check, if border's reached in any state
        for pos in self.cur_poses:
            if self.__is_field_border__(pos):
                # If yes -- then AI would measure whole position
                debug_str += 'Making measurement and exiting...'
                
                if debug:
                    print(debug_str)
                
                move = (3, None)
                self.__apply_move__(move)
                
                return move
        
        chosen_pathes = []
        shortest_path_len = 1e9
        
        # Finding the shortest pathes from all the positions
        for cur_pos in self.cur_poses:
            pathes = self.__dfs__(cur_pos)
                
            for path in pathes:
                if shortest_path_len > len(path):
                    chosen_pathes = [path[:2]]
                    shortest_path_len = len(path)
                elif shortest_path_len == len(path):
                    chosen_pathes += [path[:2]]
                    
        # if there is no legal moves -- consede
        if len(chosen_pathes) == 0:
            debug_str += 'No legal moves available. Conseding...'
                
            if debug:
                print(debug_str)
                
            move = (4, None)
            self.__apply_move__(move)
            
            return move
        
        debug_str += f'The beginnings of pathes found:\n {chosen_pathes}\n'
        debug_str += '-'*40 + '\n'
        
        # Computes set of directions, which AI want and is able to go to
        moves_dict = dict()
        
        for path in chosen_pathes:
            if not path[0] in moves_dict:
                moves_dict[path[0]] = {self.__detect_direction__(path[0], path[1])}
            else:
                moves_dict[path[0]].add(self.__detect_direction__(path[0], path[1]))
        
        debug_str += 'Moves dict:\n'
        for key in moves_dict:
            debug_str += f'    {key}\n'
            debug_str += f'        {moves_dict[key]}\n'
        debug_str += '-'*40 + '\n'
        
        desired_directions = set.intersection(*moves_dict.values())
        
        debug_str += f"Considering directions: {desired_directions}\n"
        
        possible_directions = set()
        for direction in desired_directions:
            is_possible = True
            for pos in self.cur_poses:
                if not self.__shift_in_direction__(pos, direction) in self.adj_vtx[pos]:
                    is_possible = False
                    break            
            if is_possible:
                possible_directions.add(direction)
        desired_directions &= possible_directions        
        
        debug_str += "Possibe directions: {desired_directions}\n"
        debug_str += '-'*40 + '\n'

        # Decide, which move to make
        move = tuple()
        if len(desired_directions) == 0:
            rand_vtx = sample(list(moves_dict.keys()), k=1)[0]
            rand_dir = sample(list(moves_dict[rand_vtx]), k=1)[0]
            
            if len(self.cur_poses) == 1:
                move = (0, rand_dir)
            else:
                move = (2, [rand_vtx, rand_dir])
            
        if len(desired_directions) == 1:
            move = (0, desired_directions.pop())
                
        elif len(desired_directions) > 1:
            chosen_directions = sample(list(desired_directions), k=2) 
            move = (1, chosen_directions)
            
        self.__apply_move__(move)
        
        debug_str += f'Making move: {move}\n'
        debug_str += 'New positions are:\n'
        debug_str += '    {self.cur_poses}\n'
        debug_str += '-'*40 + '\n'
        debug_str += 'Work ended!\n'
        
        if debug:
            print(debug_str)
        
        return move
            
        

## Game Engine

The following classes are responsible for linking the previous classes and working with GUI.

### Coordinates converter

We decided to use separate coordinate systems for each class, depenging on the values we mostly compute.

As an example, coordinate system of the `Cat`s' classes is the only one, which keeps an invariant of coordinates shift within each direction.

The following functions apply the transition from the main coordinate types within our program.

In [9]:
def ai_to_cat(coords):
    
    '''Convert from ai's coordinates to cat's coordinates '''
    
    new_coords = tuple()
    if coords[0] % 2 == 0:
        new_coords = (coords[0], 2*coords[1])
    else:
        new_coords = (coords[0], 2*coords[1] + 1)        
    return new_coords

def cat_to_ai(coords):
    
    '''Convert from cat's coordinates to ai's coordinates '''
    
    return (coords[0], coords[1] // 2)

def canvas_to_cat(coords):
    
    '''Convert from canvas's coordinates to cat's coordinates '''
    
    new_coords = tuple()
    if coords[1] % 2 == 0:
        new_coords = (coords[0]*2, coords[1])
    else:
        new_coords = (coords[0]*2+1, coords[1])
    return new_coords
        
def cat_to_canvas(coords):
    
    '''Convert from cat's coordinates to canvas's coordinates '''
    
    return (coords[0] // 2, coords[1])

def ai_to_canvas(coords):
    
    '''Convert from ai's coordinates to canvas's coordinates '''
    
    return cat_to_canvas(ai_to_cat(coords))

def canvas_to_ai(coords):
    
    '''Convert from canvas's coordinates to ai's coordinates '''
    
    return cat_to_ai(canvas_to_cat(coords))

In [10]:
def point_in_polygon(point, poly):
    '''
    Checks whether the given point belongs to the
    given polygon through calculation of areas.
    '''
    
    x_cl, y_cl = point
    S1 = 0.0
    S2 = 0.0
    
    # Calculate unsigned vector area
    # If the point is inside the polygon,
    # then this area will be exactly 
    # the area of a polygon
    for k in range(len(poly)):
        p0, p1 = poly[k], poly[(k + 1) % len(poly)]
        S1 += math.fabs((p0[0] - x_cl) * (p1[1] - p0[1]) - (p1[0] - p0[0]) * (p0[1] - y_cl))
    
    # Polygon area according to Green's Formula
    for k in range(len(poly)):
        S2 += (poly[k][0] * poly[(k + 1) % len(poly)][1] - poly[k][1] * poly[(k + 1) % len(poly)][0])

    return math.isclose(S1, S2)


class Drawable:
    
    '''
    This class provides the methods and parameters
    required to simplify drawing the object onto
    the screen. Since we are using the hexagonal 
    field, this class is dependent only on the
    length of the diagonal and dimensions of the sprite.
    '''

    
    def __init__(self, sprite, hex_d, h, w, i, j):
        self.sprite = iw.Image.from_file(sprite)
        self.hex_d = hex_d
        self.h = h
        self.w = w
        self.i = i
        self.j = j
        
        self.x = hex_d / 2 + j * 3 / 2*hex_d + (i % 2) * 3 / 4 * hex_d - w / 2 + hex_d / 2
        self.y = (i + 1) * hex_d*math.sqrt(3) / 4 - h / 2 + hex_d - (hex_d * math.sqrt(3) / 4)


    def draw(self, canvas):
        canvas.draw_image(self.sprite, self.x, self.y, self.h, self.w)

In [11]:
class Cat(Drawable):
    def __init__(self, sprite, hex_d, h, w, i, j):
        super(Cat, self).__init__(sprite, hex_d, h, w, i, j)

In [12]:
class Dog(Drawable):
    def __init__(self, sprite, hex_d, h, w, i, j):
        super(Dog, self).__init__(sprite, hex_d, h, w, i, j)

In [13]:
class GameEngine:
    
    '''
    This class is responsible for both game engine
    and graphics engine. It's internals contain
    interactable canvas, obstacles list, main
    character and graph logic.
    '''
    
    def __init__(self, hex_d = 60, f_h = 10, f_w = 5):
        self.hex_d = hex_d
        self.f_h = f_h
        self.f_w = f_w
        self.dog_list = []
        self.cur_player = 0
        self.active = 1
        coeff = 0.3
        self.cat = Cat("emoji-cat.png", 
                       self.hex_d, 
                       self.hex_d * 5/ 6, 
                       self.hex_d * 5/ 6, 
                       random.randint(int(self.f_h * (1 - coeff) / 2), int(self.f_h * (1 - coeff))), 
                       random.randint(int(self.f_w * (1 - coeff) / 2), int(self.f_w * (1 - coeff))))
        
        self.simcat = SimulatorCat(lim=canvas_to_cat((f_w, f_h)), init_pos=canvas_to_cat((self.cat.j, self.cat.i)))
        self.enai = AI(lim=canvas_to_ai((self.f_w, self.f_h)), init_pos=canvas_to_ai((self.cat.j, self.cat.i)))
        self.canvas = None
        
        # self.cat_init()
        self.generate_field()
        self.init_canvas()
        
    
    # Randomly place the cat into the field
    def cat_init(self):
        coeff = 0.3
        self.cat = Cat("emoji-cat.png", 
                       self.hex_d, 
                       self.hex_d * 5/ 6, 
                       self.hex_d * 5/ 6,
                       random.randint(int(self.f_h * (1 - coeff) / 2), int(self.f_h * (1 - coeff))), 
                       random.randint(int(self.f_w * (1 - coeff) / 2), int(self.f_w * (1 - coeff))))
    
    # Generate every vertex of the field
    def generate_field(self):
        # Hexagon is generated as the following:
        # We take a zero vector with the length of 
        # hexagons diagonal. Then we make
        # rotations in complex plane on pi / 3
        # until we get all the necessary vertexes
        z = complex(-self.hex_d / 2, 0) 
        rot = cmath.exp(3.1415926 / 3 * complex(0, 1))
        hex_vertices = [((z * rot**i).real, (z * rot**i).imag) for i in range(0, 6)]
        
        # The field is simply needed amount of hexagons
        # placed according to formulas to form a field
        self.hex_field = []
        for i in range(self.f_h):
            row = []
            for j in range(self.f_w):
                row.append(list(map(lambda p: 
                                    (p[0] + 3 / 4 * self.hex_d * (i % 2) + 3 / 2 * self.hex_d * j, 
                                     p[1] + math.sqrt(self.hex_d**2 / 4 - self.hex_d**2 / 16) * i), 
                                    hex_vertices)))
            self.hex_field.append(row)
    
    # Initializing graphics engine as a MultiCanvas
    # canvas[0] is the field (not frequently updated)
    # canvas[1] is the cat (updated on every step)
    # canvas[2] is obstacles layer (updated on every step)
    # canvas[3] is reserved layer for any extras 
    # (i.e. highlighting selected hexagon)
    def init_canvas(self):   
        """
        It is a callback function called every time 
        assigned canvas receives a mousedown event.
        """
        def mousedown_callback(x_cl, y_cl):
            if self.cur_player == 1:
                return
            
            # Offset coordinates converted to field coordinates
            x_cl -= self.hex_d
            y_cl -= self.hex_d

            # Row number starting from -1
            y_i = int(y_cl // (math.sqrt(3) * self.hex_d / 4))

            # Check every hex in two possible rows
            for j in range(self.f_w):
                hex1 = self.hex_field[y_i + 0][j]
                hex2 = self.hex_field[y_i + 1][j]

                i = -1 # Future row number

                # Check possible hexagons
                if point_in_polygon((x_cl, y_cl), hex1):
                    i = y_i
                elif point_in_polygon((x_cl, y_cl), hex2):
                    i = y_i + 1

                # If row was found, then append dogs
                if i >= 0:
                    if canvas_to_ai((j, i)) in self.enai.cur_poses:
                        return
                    for dog in self.dog_list:
                        if dog.i == i and dog.j == j:
                            return
                        
                    self.cur_player = 1
                    self.enai.remove_vertex(canvas_to_ai((j, i)))
                    self.dog_list.append(
                        Dog("emoji-dog.png", 
                            self.hex_d, 
                            self.hex_d / 2,
                            self.hex_d / 2, i, j))
                    self.dog_list[-1].draw(self.canvas[2])
                    
        self.canvas = ic.MultiCanvas(4, width = 1.75 * (self.f_w) * self.hex_d, 
                                     height = 0.6 * (self.f_h) * self.hex_d)
        self.canvas.on_mouse_down(mousedown_callback)
        # Stroke every hexagon in the field
        for row in self.hex_field:
            for hex in row:
                self.canvas[0].stroke_polygon(list(map(lambda p: (p[0] + self.hex_d, p[1] + self.hex_d), hex)))
        
        self.cat.draw(self.canvas[1])
        self.init_dogs()
    
    # Fills the field with obstacles
    def init_dogs(self):
        pass
    
    def restart(self):
        self.dog_list.clear()
        self.cur_player = 0
        self.active = 1
        coeff = 0.3
        self.cat = Cat("emoji-cat.png", 
                       self.hex_d, 
                       self.hex_d * 5 / 6, 
                       self.hex_d * 5 / 6, 
                       random.randint(int(self.f_h * (1 - coeff) / 2), int(self.f_h * (1 - coeff))), 
                       random.randint(int(self.f_w * (1 - coeff) / 2), int(self.f_w * (1 - coeff))))
        
        self.simcat = SimulatorCat(lim=canvas_to_cat((self.f_w, self.f_h)), init_pos=canvas_to_cat((self.cat.j, self.cat.i)))
        self.enai = AI(lim=canvas_to_ai((self.f_w, self.f_h)), init_pos=canvas_to_ai((self.cat.j, self.cat.i)))
        
        self.canvas[1].clear()
        self.canvas[2].clear()
        self.cat.draw(self.canvas[1])
        
    
    def make_measurement_move(self):
        pos1 = self.simcat.measure_position()
        self.enai.cat_measured(cat_to_ai(pos1))
        
        self.canvas[1].clear()
        for pos in self.enai.cur_poses:
            cpos = ai_to_canvas(pos)
            Cat("emoji-cat.png", 
                self.hex_d,
                self.hex_d * 5 / 6,
                self.hex_d * 5 / 6,
                cpos[1], cpos[0]).draw(self.canvas[1])
            
    def make_move(self):
        move = self.enai.make_move()
        pos1 = (0, 0)
        if move[0] == 4:
            return move
        if move[0] == 3:
            pos1 = self.simcat.measure_position()
            self.enai.cat_measured(cat_to_ai(pos1))
        elif move[0] == 0:
            self.simcat.move(move[1])
        elif move[0] == 1:
            self.simcat.superposition_move(move[1])
        elif move[0] == 2:
            self.simcat.entangled_move(ai_to_cat(move[1][0]), move[1][1])
        
        freq_dict = dict()
        for pos in self.enai.cur_poses:
            if not pos in freq_dict:
                freq_dict[pos] = 1
            else:
                freq_dict[pos]+=1
        
        total_poses = len(self.enai.cur_poses)
        
        self.canvas[1].clear()
        for pos in self.enai.cur_poses:
            cpos = ai_to_canvas(pos)
            Cat("emoji-cat.png", 
                self.hex_d,
                self.hex_d * 5 / 6 * freq_dict[pos] / total_poses,
                self.hex_d * 5 / 6 * freq_dict[pos] / total_poses,
                cpos[1], cpos[0]).draw(self.canvas[1])
        
        return move
        
    
        

# Game Loop

This function implements a game loop. Enjoy the game!

In [14]:


def run_game(field_width = 30, field_height = 15):
    engine = GameEngine(hex_d = 30, f_h = field_width, f_w = field_height)
    
    engine.simcat.show_circuit().savefig('savedfig.png')
    with open("savedfig.png", 'rb') as file:
        image = file.read()
    circuit = iw.Image(value=image, layout=iw.Layout(min_height = '25%', min_width = '25%', max_height = "25%", max_width = "25%"))
    
    cat_moves = iw.HTML("Cat moves logs:<br>")
    lose_label = iw.HTML("""<h1>You lost( </h1>""")
    win_label = iw.HTML("""<h1> You won! </h1>""")
    r_but = iw.Button(description="Restart")
    s_but = iw.Button(description="Exit")
    m_but = iw.Button(description="Measure")
    sc_but = iw.Button(description="Show Circuit")

    game_vbox = iw.VBox([engine.canvas, iw.HBox([r_but, m_but, sc_but, s_but]), circuit, cat_moves])
    lose_vbox = iw.VBox([lose_label, s_but])
    win_vbox = iw.VBox([win_label, s_but])
    
    screen_vbox = game_vbox
    
    def inactive_callback(b):
        engine.active = 0
        screen_vbox.close()
    def restart_callback(b):
        engine.restart()
    def measure_callback(b):
        engine.make_measurement_move()
        engine.cur_player = 1
    def show_circuit_callback(b):
        os.remove('savedfig.png')
        engine.simcat.show_circuit().savefig('savedfig.png')
        with open("savedfig.png", 'rb') as file:
            image = file.read()
        circuit.value = image
    def gameover():
        time.sleep(2)
        engine.active = 0
        screen_vbox.children = lose_vbox.children
    def win():
        time.sleep(2)
        engine.active = 0
        screen_vbox.children = win_vbox.children
    def ai_worker():
        while engine.active == 1:
            if engine.cur_player == 1:
                move = engine.make_move()
                debug_str = ''
                if move[0] == 0:
                    debug_str = f"  Simple move in direction {move[1]}<br>"
                elif move[0] == 1:
                    debug_str = f"  Superposition of moves in directions {move[1]}<br>"
                elif move[0] == 2:
                    debug_str = f"  Entangled move from {move[1][0]} in direction {move[1][1]}<br>"
                elif move[0] == 3:
                    debug_str = "  Measure the position<br>"
                elif move[0] == 4:
                    cat_moves.value += "  No more pathes to the exit. Player won<br>"
                    win()
                cat_moves.value += debug_str
                engine.cur_player = 0
            else:
                time.sleep(0.5)
    def game_end_worker():
        while engine.active == 1:  
            if len(engine.enai.cur_poses) == 1:
                pos = engine.enai.cur_poses[0]
                if pos[0] == 0 or pos[0] == engine.enai.lim[0]-1 or pos[1] == 0 or pos[1] == engine.enai.lim[1]-1:
                    gameover()
            else:
                time.sleep(0.5)
    
    r_but.on_click(restart_callback)
    s_but.on_click(inactive_callback)
    m_but.on_click(measure_callback)
    sc_but.on_click(show_circuit_callback)
    
    ai_thread = threading.Thread(target=ai_worker)
    game_end_thread = threading.Thread(target=game_end_worker)
    game_end_thread.start()
    ai_thread.start()
    
    display(screen_vbox)

### Game rules

**Goal of the game:** trap the cat, so that it could not reach the borders and ran away.

**What you can do during the move:** 
 * Put the dogs on the field
 * Measure the position of the cat

**What you also can do:** restart the game, exit the game and check the circuit, which represents current cat position

**What cat can do,** the most tricky part:
 * Move as a usual cat
 * Make a superposition of moves. For example, go in direction 0 and 3. Notice, that:
     * Superposition applies to all cat's superpositions.
     
     * Superpositions could intersect. In this case, the probability of this position would double.
     
     * If cat is in a superposition, *usual move applies to all superpositions at the same time*
 * Make an entangled move from a certain position in a certain direction
 
**Tricky moments:**
 * Sometimes you need to wait a bit (sometime it's on purpose, sometimes -- not)
 * Do not stop the cell execution/leave the game without exiting
 * Possible bug: in case the first game did not end, exit it and try again. In 100% of cases it helps
 
**That's all. Good luck!**

In [16]:
# Advice: exit the first game immideately to avoid any possible bugs
run_game(20, 10)